In [2]:
import re
import pandas
import requests
from bs4 import BeautifulSoup
import matplotlib.pyplot as plt
from matplotlib import font_manager


def get_html(url):
    try:
        r = requests.get(url)  # 使用get来获取网页数据
        r.raise_for_status()  # 如果返回参数不为200，抛出异常
        r.encoding = r.apparent_encoding  # 获取网页编码方式
        return r.text  # 返回获取的内容
    except:
        return '错误'


def save(html):
    # 解析网页
    soup = BeautifulSoup(html, 'html.parser')  # 指定Beautiful的解析器为“html.parser”

    # 定义好相关列表准备存储相关信息
    TScore = []  # 综合评分
    name = []  # 动漫名字
    bfl = []  # 播放量
    pls = []  # 评论数
    scs = []  # 收藏数

    # ********************************************  动漫名字存储
    for tag in soup.find_all('div', class_='info'):
        # print(tag)
        bf = tag.a.string
        name.append(str(bf))
    print(name)

    # ********************************************  播放量存储
    for tag in soup.find_all('div', class_='detail'):
        # print(tag)
        bf = tag.find('span', class_='data-box').get_text()
        # 统一单位为‘万’
        if '亿' in bf:
            num = float(re.search(r'\d(.\d)?', bf).group()) * 10000
            # print(num)
            bf = num
        else:
            bf = re.search(r'\d*(\.)?\d', bf).group()
        bfl.append(float(bf))
    print(bfl)
    # ********************************************  评论数存储
    for tag in soup.find_all('div', class_='detail'):
        # pl = tag.span.next_sibling.next_sibling
        pl = tag.find('span', class_='data-box').next_sibling.next_sibling.get_text()
        # *********统一单位
        if '万' not in pl:
            pl = '%.1f' % (float(pl) / 10000)
            # print(123, pl)
        else:
            pl = re.search(r'\d*(\.)?\d', pl).group()
        pls.append(float(pl))
    print(pls)
    # ********************************************  收藏数
    for tag in soup.find_all('div', class_='detail'):
        sc = tag.find('span', class_='data-box').next_sibling.next_sibling.next_sibling.next_sibling.get_text()
        sc = re.search(r'\d*(\.)?\d', sc).group()
        scs.append(float(sc))
    print(scs)
    # ********************************************  综合评分
    for tag in soup.find_all('div', class_='pts'):
        zh = tag.find('div').get_text()
        TScore.append(int(zh))
    print('综合评分', TScore)

    # 存储至excel表格中
    info = {'动漫名': name, '播放量(万)': bfl, '评论数(万)': pls, '收藏数(万)': scs, '综合评分': TScore}
    dm_file = pandas.DataFrame(info)
    dm_file.to_excel('Dongman.xlsx', sheet_name="动漫数据分析")
    # 将所有列表返回
    return name, bfl, pls, scs, TScore


def view(info):
    my_font = font_manager.FontProperties(fname='./data/STHeiti Medium.ttc')  # 设置中文字体（图标中能显示中文）
    dm_name = info[0]  # 番剧名
    dm_play = info[1]  # 番剧播放量
    dm_review = info[2]  # 番剧评论数
    dm_favorite = info[3]  # 番剧收藏数
    dm_com_score = info[4]  # 番剧综合评分
    # print(dm_com_score)

    # 为了坐标轴上能显示中文
    plt.rcParams['font.sans-serif'] = ['SimHei']
    plt.rcParams['axes.unicode_minus'] = False

    # **********************************************************************综合评分和播放量对比
    # *******综合评分条形图
    fig, ax1 = plt.subplots()
    plt.bar(dm_name, dm_com_score, color='red')  #设置柱状图
    plt.title('综合评分和播放量数据分析', fontproperties=my_font)  # 表标题
    ax1.tick_params(labelsize=6)
    plt.xlabel('番剧名')  # 横轴名
    plt.ylabel('综合评分')  # 纵轴名
    plt.xticks(rotation=90, color='green')  # 设置横坐标变量名旋转度数和颜色

    # *******播放量折线图
    ax2 = ax1.twinx()  # 组合图必须加这个
    ax2.plot(dm_play, color='cyan')  # 设置线粗细，节点样式
    plt.ylabel('播放量')  # y轴

    plt.plot(1, label='综合评分', color="red", linewidth=5.0)  # 图例
    plt.plot(1, label='播放量', color="cyan", linewidth=1.0, linestyle="-")  # 图例
    plt.legend()

    plt.savefig(r'E:1.png', dpi=1000, bbox_inches='tight')  #保存至本地

    # plt.show()

    # **********************************************************************评论数和收藏数对比
    # ********评论数条形图
    fig, ax3 = plt.subplots()
    plt.bar(dm_name, dm_review, color='green')
    plt.title('番剧评论数和收藏数分析')
    plt.ylabel('评论数（万）')
    ax3.tick_params(labelsize=6)
    plt.xticks(rotation=90, color='green')

    # *******收藏数折线图
    ax4 = ax3.twinx()  # 组合图必须加这个
    ax4.plot(dm_favorite, color='yellow')  # 设置线粗细，节点样式
    plt.ylabel('收藏数（万）')

    plt.plot(1, label='评论数', color="green", linewidth=5.0)
    plt.plot(1, label='收藏数', color="yellow", linewidth=1.0, linestyle="-")
    plt.legend()
    plt.savefig(r'E:2.png', dpi=1000, bbox_inches='tight')

    # **********************************************************************综合评分和收藏数对比
    # *******综合评分条形图
    fig, ax5 = plt.subplots()
    plt.bar(dm_name, dm_com_score, color='red')
    plt.title('综合评分和收藏数量数据分析')
    plt.ylabel('综合评分')
    ax5.tick_params(labelsize=6)
    plt.xticks(rotation=90, color='green')

    # *******收藏折线图
    ax6 = ax5.twinx()  # 组合图必须加这个
    ax6.plot(dm_favorite, color='yellow')  # 设置线粗细，节点样式
    plt.ylabel('收藏数（万）')
    plt.plot(1, label='综合评分', color="red", linewidth=5.0)
    plt.plot(1, label='收藏数', color="yellow", linewidth=1.0, linestyle="-")
    plt.legend()

    plt.savefig(r'E:3.png', dpi=1000, bbox_inches='tight')

    # **********************************************************************播放量和评论数对比
    # *******播放量条形图
    fig, ax7 = plt.subplots()
    plt.bar(dm_name, dm_play, color='cyan')
    plt.title('播放量和评论数 数据分析')
    plt.ylabel('播放量（万）')
    ax7.tick_params(labelsize=6)
    plt.xticks(rotation=90, color='green')

    # *******评论数折线图
    ax8 = ax7.twinx()  # 组合图必须加这个
    ax8.plot(dm_review, color='green')  # 设置线粗细，节点样式
    plt.ylabel('评论数（万）')
    plt.plot(1, label='播放量', color="cyan", linewidth=5.0)
    plt.plot(1, label='评论数', color="green", linewidth=1.0, linestyle="-")
    plt.legend()
    plt.savefig(r'E:4.png', dpi=1000, bbox_inches='tight')

    plt.show()


def main():
    url = 'https://www.bilibili.com/v/popular/rank/bangumi'  # 网址
    html = get_html(url)  # 获取返回值
    # print(html)
    info = save(html)
    view(info)


if __name__ == '__main__':
    main()


['盾之勇者成名录 第二季', '约会大作战 第四季', '恋爱游戏世界对路人角色很不友好', '测不准的阿波连同学', '鬼灭之刃 游郭篇', 'RPG不动产', '恋爱要在世界征服后', '夏日幻魂', '处刑少女的生存之道', '理科生坠入情网，故尝试证明。 第二季', '鬼灭之刃 无限列车篇 中配版', '擅长捉弄的高木同学 第三季', '盾之勇者成名录', '国王排名', 'JOJO的奇妙冒险 石之海', '现实主义勇者的王国再建记', '与变成了异世界美少女的好友一起冒险', '咒术回战', '上班族想被治愈', '黑色四叶草', '天才王子的赤字国家振兴术', '明日酱的水手服', '瓦尼塔斯的手记', '鬼灭之刃', '指名！', '博人传 火影忍者新时代', '通灵王', '失格纹的最强贤者～世界最强的贤者为了变得更强而转生了～', '小林家的龙女仆', 'JOJO的奇妙冒险 黄金之风', '名侦探柯南', '关于我转生变成史莱姆这档事 第二季', 'OVERLORD', '鬼灭之刃 无限列车篇', '四月是你的谎言', 'OVERLORD Ⅲ', '白领羽球部', '堀与宫村', 'OVERLORD Ⅱ', '秘密内幕 女警的反击', '女孩的钓鱼慢活', '关于我转生变成史莱姆这档事', '里亚德录大地', '不能播放', '自称贤者弟子的贤者', '半妖的夜叉姬 第二季']
[2.0, 2.0, 2.0, 2.0, 5.0, 2.0, 2.0, 1.0, 2.0, 2.0, 1.0, 12.0, 25.0, 23.0, 12.0, 26.0, 12.0, 24.0, 2.0, 170.0, 12.0, 3.0, 20.0, 26.0, 13.0, 235.0, 45.0, 12.0, 14.0, 39.0, 1095.0, 24.0, 13.0, 7.0, 22.0, 13.0, 7.0, 13.0, 13.0, 13.0, 10.0, 29.0, 12.0, 5.0, 12.0, 18.0]
[1437.2, 984.1, 364.0, 1428.1, 9039.5, 217.4, 277.1, 174.9, 466.2, 728.8, 516.5, 4911.9, 2.7, 4.7, 1.1, 6736.0, 4728.3, 6.8, 3

AttributeError: 'NoneType' object has no attribute 'next_sibling'